In [1]:
import h5py
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit
import scipy.stats
import numpy as np
from glob import glob

In [2]:
files = glob("/project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_*.h5")

In [3]:
GAIN = 4/1e3
MeVToElectrons = 4.237e+04

In [4]:
dQ = np.array([])
dx = np.array([])

files = glob("/project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_*.h5")

for filename in files[2:10]:
    print("Scanning file %s..." % filename)
    track_file = h5py.File(filename, "r")
    events = track_file['events']
    tracks = track_file['tracks']

    for event in events:
        if event['nhit'] < 100:
            continue

        for track in tracks[event['track_ref']]:
            
            if track['nhit'] < 50 or np.any(track['residual'] > 2):
                continue
            dQ = np.append(dQ, track['q']/GAIN)
            dx = np.append(dx, track['length'])

    track_file.close()

Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_20_58_27_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_20_48_36_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_21_10_59_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_21_02_51_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_20_58_47_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_23_39_58_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_20_07_54_CESTevd.h5...
Scanning file /project/projectdirs/dune/www/data/Module0/TPC1+2/dataRuns/tracksData/datalog_2021_04_03_01_35_44_CESTev

In [5]:
dQdx = dQ/dx
recomb_factor = 0.6980
mm2cm = 10
dEdx = dQdx / MeVToElectrons / recomb_factor * mm2cm

In [7]:
%matplotlib widget

fig, ax = plt.subplots(1,1)
n, binedges, patches = ax.hist(dEdx, range=(0,6),bins=120, histtype='step', color='k', lw=2, label='Data')
bincenters = np.mean(np.vstack([binedges[0:-1],binedges[1:]]), axis=0)
dx = bincenters[1]-bincenters[0]
ax.errorbar(bincenters, n, yerr=np.sqrt(n), ls='none', lw=2, c='k')

def moyalgauss(x, A, mu, scale, sigma):
    global dx
    return A*np.convolve(scipy.stats.moyal.pdf(x,mu,scale), scipy.stats.norm.pdf(x,mu,sigma), mode="same") * dx


coeff, pcov = curve_fit(moyalgauss, bincenters, n, 
                        p0=(800,3,0.4,0.1),maxfev=5000)
x=np.linspace(0,6,6000)
# ax.hist(dEdx,bins=100,range=(0,8))
ax.set_xlabel("dE/dx [MeV/cm]")
ax.plot(bincenters,moyalgauss(bincenters,*coeff), lw=2, ls='--',c='r', 
        label='Fit MPV = %.3f MeV/cm' % x[np.argmax(moyalgauss(x,*coeff))])
ax.legend()
ax.set_ylim(0,3400)
ax.set_xlim(0.5,5)
ax.set_ylabel('N. tracks / 0.1 MeV/cm')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0, 0.5, 'N. tracks / 0.1 MeV/cm')

In [9]:
print(coeff)

[1.77463163e+03 2.54800112e+00 1.36281486e-01 9.32531689e-02]
